<a href="https://colab.research.google.com/github/skdldbwls/predict_mbti_korean/blob/master/crawling_%26_make_data.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# crawling

In [ ]:
!pip install selenium
!apt-get update # to update ubuntu to correctly run apt install
!apt install chromium-chromedriver

     |████████████████████████████████| 911kB 5.6MB/s 
Get:1 https://cloud.r-project.org/bin/linux/ubuntu bionic-cran40/ InRelease [3,626 B]
Ign:2 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  InRelease
Get:3 http://security.ubuntu.com/ubuntu bionic-security InRelease [88.7 kB]
Get:4 https://cloud.r-project.org/bin/linux/ubuntu bionic-cran40/ Packages [41.5 kB]
Ign:5 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  InRelease
Hit:6 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  Release
Hit:7 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  Release
Get:8 http://ppa.launchpad.net/c2d4u.team/c2d4u4.0+/ubuntu bionic InRelease [15.9 kB]
Hit:10 http://archive.ubuntu.com/ubuntu bionic InRelease
Get:12 http://archive.ubuntu.com/ubuntu bionic-updates InRelease [88.7 kB]
Hit:13 http://ppa.launchpad.net/cran/libgit2/ubuntu bionic InRelease
Get:14 http://security.

In [ ]:
import os
from bs4 import BeautifulSoup
from selenium import webdriver
from pandas import Series, DataFrame
import pandas as pd
import time
import re
from tqdm import tqdm_notebook

chrome_options = webdriver.ChromeOptions()
chrome_options.add_argument('--headless') #내부 창을 띄울 수 없으므로 설정
chrome_options.add_argument('--no-sandbox')
chrome_options.add_argument('--disable-dev-shm-usage')
wd = webdriver.Chrome('chromedriver',chrome_options=chrome_options)

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:14: DeprecationWarning: use options instead of chrome_options
  


In [ ]:
categories = ['ISTJ', 'ISFJ', 'ESTJ', 'ESFJ', 'ISTP', 'ESTP', 'ESFP','ISFP', 
              'INTJ','INTP','ENTJ', 'ENTP', 'INFJ','INFP','ENFJ','ENFP']

In [ ]:
def crawler(url_sub):
  contents = []
  names = []
  sub_names = []
  for link in tqdm_notebook(url_sub):
    try:
      # print(link)
      wd.get(link)
      time.sleep(1)
      wd.switch_to.frame('cafe_main')
      time.sleep(1)
      soup = BeautifulSoup(wd.page_source, 'lxml')
      contentArea = soup.find('div', {'class':'article_viewer'})
      parags = contentArea.findAll('p')  
      content = ""
      #print(parags)
      for parag in parags:
          content += parag.text.strip()
      contents.append(content)

      nameArea = soup.find('div', {'class':'nick_box'})
      name_parags = nameArea.findAll('a')  
      name = ""
      # print(parags)
      for parag in name_parags:
          name += parag.text.strip()
      names.append(name)

      sub_name = re.sub('[^a-zA-Z]','',name.upper())
      sub_names.append(sub_name)
      
      pass
    except:
      # Continue to next iteration.
      continue

  return contents, names, sub_names

### crawl_make_dataframe 함수

sub_name : user_id에서 mbti가 있는 닉네임만 추출하기 위해 따로 컬럼을 만들어줌

여기에서 바로 type(mbti)컬럼을 만들 수 있지만 나중에 잘못되었을 경우를 대비해 하나의 컬럼으로 남겨놓음

In [ ]:
def crawl_make_dataframe(url_page, start, end):
    for i in range(start, end+1, 1):
      print(i)
      wd.get(url_page + str(i))  #mbti카페 - 신변 잡기 카테고리
      time.sleep(1)
      wd.switch_to.frame('cafe_main')  #카페 메인 아이프레임
      html = wd.page_source  #페이지 소스 가져오기
      #print(html)
      # wd.close()

      soup = BeautifulSoup(html, "html.parser")

      title = soup.select('.inner_list')

      url_sub = [] # 각 게시물 url 뽑음
      for link in title:
        # print(link)
        linkadd = link.find("a")['href']
        url_sub.append("https://cafe.naver.com" + linkadd)
        
      df1, df2, df3 = crawler(url_sub)
      df1 = pd.DataFrame(data = df1, columns=['posts'])
      df2 = pd.DataFrame(data = df2, columns=['user_name'])
      df3 = pd.DataFrame(data = df3, columns=['sub_name'])
      add = pd.concat([df2, df3, df1], axis=1)

      if i == start:
        df = add
      else:
        df = pd.concat([df, add], axis=0)
      #print(df['user_name'])
      #print(df['sub_name'])

      df = df.loc[df['sub_name'].str.contains(categories[0], case=False)| #case = False : 대소문자 구분 없이
          df['sub_name'].str.contains(categories[1], case=False)|
          df['sub_name'].str.contains(categories[2], case=False)|
          df['sub_name'].str.contains(categories[3], case=False)|
          df['sub_name'].str.contains(categories[4], case=False)|
          df['sub_name'].str.contains(categories[5], case=False)|
          df['sub_name'].str.contains(categories[6], case=False)|
          df['sub_name'].str.contains(categories[7], case=False)|
          df['sub_name'].str.contains(categories[8], case=False)|
          df['sub_name'].str.contains(categories[9], case=False)|
          df['sub_name'].str.contains(categories[10], case=False)|
          df['sub_name'].str.contains(categories[11], case=False)|
          df['sub_name'].str.contains(categories[12], case=False)|
          df['sub_name'].str.contains(categories[13], case=False)|
          df['sub_name'].str.contains(categories[14], case=False)|
          df['sub_name'].str.contains(categories[15], case=False)
          ] 

    return df


## 사랑방 카테고리 크롤링

#### INFJ ♡ ENFJ
 34 - 344

<첫 글 >

다른 엔프제분들도 이러신가요? [9]	
쀼ENFJ
2020.10.31.	

In [ ]:
INFJ_ENFJ = crawl_make_dataframe('https://cafe.naver.com/ArticleList.nhn?search.clubid=11856775&search.menuid=14&search.boardtype=L&search.totalCount=151&search.page=', 34, 344)

34


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:5: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  """



35



36



37


...


340



341



342



343



344


In [ ]:
INFJ_ENFJ

user_name  ...                                              posts
0              쀼ENFJ  ...  저는 제가 애교가 없다고 생각하는데 사람들이 제가 애교가 엄청 많대요.말할때 자연스...
1           INFJ젤레이나  ...  인프제에게 음악 추천합니다​​​윤하 퍼레이드, 레인보우, 스트로베리데이즈, 에어플레...
3       제이크 ENFJ 4w3  ...                여자친구가 그린 저희 모습인데 맨날 저보고 대형견같대요 ㅎㅎ..
4            안녕 INFJ  ...  전 엄청 조용한편 이거든요.가족들이 매우매우매우 말이 많은편인데다가,저는 매우매우매...
5        infj 길박 5w6  ...  기브앤 테이크가 안되서.돈이나 물질적인 얘기는 하지말자.그건 어찌보면 너무나 당연한...
..               ...  ...                                                ...
11          미녀는풀infj  ...  transform1. 변형시키다개쌍욕은 아니고 캐성질을, 개꼬장을..보았다.뿌듯했다...
1          은빛겨울 INFJ  ...  음...... 우선 글쓴분이 INFJ가 아니라고 가정하고.....INFJ의 애정 표...
1           미녀는풀infj  ...  개인적으로 죽고자 하는 사람은 살고살고자 하는 사람은 죽는다고 하므로,연애를 하고자...
0   비빔밥 ENTP Sc4H5L5  ...  신해철, 박진영, 프로이드, 그리고 카메론.어떤 공통점이 보이는 것 같지 않나요?"...
0           메칸더 INFJ  ...  연말입니다. 잘 지내시나요. 건강들하신가요..막장을 달린지도 어언 햇수로 2년이 넘...

[1890 rows x 3 columns]

In [ ]:
INFJ_ENFJ.to_csv('INFJ_ENFJ.csv',encoding='utf-8-sig',index=False)

#### ISFJ ♡ ESFJ

첫게시물

	
Enfp어떤부분 신경써야하나여? [31]	
잇잇프프제제
2020.11.05.	

In [ ]:
ISFJ_ESFJ = crawl_make_dataframe('https://cafe.naver.com/ArticleList.nhn?search.clubid=11856775&search.menuid=13&search.boardtype=L&search.totalCount=151&search.page=', 21, 99)

21


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:5: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  """



22



23



24


...


95



96



97



98



99


In [ ]:
ISFJ_ESFJ.to_csv('ISFJ_ESFJ.csv',encoding='utf-8-sig',index=False)

In [ ]:
ISFJ_ESFJ

user_name  ...                                              posts
2       Entp입니다리  ...  자꾸 먹을거 챙겨주고자꾸 챙겨주고나 자꾸 관찰하고 칭찬해주고 엄청 섬세한데이러면 나...
3      천생연분 isfp  ...                                   sf 감성녀들 만나고싶다...
4    댄츠 ESTPd8w9  ...         한명은 완전 공감쩔고한명은 이성적인편이 좀더 강한데이유형 커플 보신적있나요?
6        Isfj달나라  ...  혹시 커플이 있다면 도움이 될까해서 써봐요.잇프제라 좋아요 누르기 전문이지만요......
8        율뚱 ENFP  ...                               ​할까말까 할때 하시는 편이신가요?!
..           ...  ...                                                ...
5     세피카 ISFJ 9  ...  카페에 SFJ를 검색하고 있는데... 참... ㅠ_ㅠ가식적이고, 답답하고, 짜증나는...
6   ISTP Student  ...     그 비관하는글뒤에에 자신을 높게평가하는의식이있을텐데??????????????????
7       세피카 ISFJ  ...  왠지 눈팅족은 상당히 많을 것 같은데...딱 하나 차이인 INFJ은 굉장히 많이 보...
10   땡이 ISFJ 6w5  ...       ISFJ 분들 책 좋아하시나요?좋아하신다면 어떤 장르 좋아하시는지 궁금해요.ㅎㅎ
1      브라우니 ISFJ  ...  안녕하세요 ^_^;몇일전에 그 주제로 친구들과 밥먹으면서 대화를 나눴는대요... 생...

[549 rows x 3 columns]

#### INTJ ◇ ENTJ

375768	
entj분들 선물 관련 질문 드립니다... [16]	
ENfJ의 하루
2020.11.03.

In [ ]:
INTJ_ENTJ = crawl_make_dataframe('https://cafe.naver.com/ArticleList.nhn?search.clubid=11856775&search.menuid=12&search.boardtype=L&search.totalCount=151&search.page=', 32, 306)

32


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:5: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  """



33



34



35


...


302



303



304



305



306


In [ ]:
INTJ_ENTJ.to_csv('INTJ_ENTJ.csv',encoding='utf-8-sig',index=False)

In [ ]:
INTJ_ENTJ

user_name sub_name                                              posts
0        소인수INTJ     INTJ  상황 : 조금 부족한 팀원들을 데리고 조별과제를 해야 할 때​ENTJ : 따라와 멍...
1       상큼발랄INFJ     INFJ  칭찬 받으면 안 기뻐요 인티제는?​기쁘게 해주고 싶고 제 애정을 전하고 싶은데 방법...
2       쌍쌍바 entp     ENTP  INTJ여자친구에게 아름답다고 말했을 때 전후사진trust->thrusth붙이지마!...
3        QUEENTJ  QUEENTJ  ENTJ 썸남 ENTJ 썸녀입니다 ...아 짜증나요​말은 절 좋아하는데행동은 절 좋...
4   빨간점 INTP 5w4    INTPW  항상 묘사되는 인티제 이미지가​무관심, 무기력, 냉소적 등등​힘앓이 없는 느낌인데,...
..           ...      ...                                                ...
4       가없는 INTJ     INTJ  정과 사를 떠나서 이건 교육의 불평등이다. 왜 학교 교과목에'옷입는 방법'이 없는가...
5       가없는 INTJ     INTJ  물질과 물체는 단순하게 물物이다.생명체는 유기체이고,식물은 정적인 생명체이며동물은 ...
0       가없는 INTJ     INTJ  존경사랑너가 나를 존경하지 않으면 나는 너를 사랑하지 않는다.내 너를 사랑하지 않으...
1       가없는 INTJ     INTJ  차에서 죽은 다이애나 왕세자비, 자신을 증언하다앵글로 색슨 영국과 미국, 사실상 현...
2       가없는 INTJ     INTJ  <<  가공의 불륜 그 실질  >>너희가 과연 영혼을 모른다고 치고서.마음과 몸은 ...

[1747 rows x 3 columns]

#### ISTJ ◇ ESTJ

	
estj여자입니다[연애상담받음] [9]	
estj쁑
2020.11.02.	

In [ ]:
ISTJ_ESTJ = crawl_make_dataframe('https://cafe.naver.com/ArticleList.nhn?search.clubid=11856775&search.menuid=11&search.boardtype=L&search.totalCount=151&search.page=',17 ,103 )

17


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:5: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  """



18



19



20


...


99



100



101



102



103


In [ ]:
ISTJ_ESTJ.to_csv('ISTJ_ESTJ.csv',encoding='utf-8-sig',index=False)

In [ ]:
ISTJ_ESTJ

user_name  sub_name                                              posts
0          estj쁑      ESTJ               다들 물어보고싶으신거 있음 물어봐주세요~!! 참고로 b형입니다~~
4       무욕커 istj      ISTJ                        이 노래를 들으면누군가는 위로를누군가는 반성을​​
10       ESTJ 라잇      ESTJ  철벽이고 밀당 잘 안 통하는 사람 나야나!남자애가 그러더라구여 저는 밀당이 통하지 ...
11       애플 ESTJ      ESTJ                           ESTJ 바람기가 어는 정도로 생각되시나요?
12    톨 isfj 2w1     ISFJW  유형 1.​말이 없고, 잘 웃지도 않고 리액션도 없는데 얼굴이 예쁨​유형 2.​분위...
..           ...       ...                                                ...
6       기파랑 INFJ      INFJ  나는 이 카페서 글보고 덧글달고 글쓰는 반면옆의 친구(ISTJ)는 축구보고 뉴스보고...
7      ENFJ MABY  ENFJMABY  10년넘은 친구가 있는데 그친구의 성격으로 제가 추측해봤을 때 그 친구는 E*FP였...
1         INFJ성년      INFJ  구성지음, 갈라놓음. istj가 아닐까요.어느날 제가 목이 말라서 친구녀석에게 물좀...
2   폭풍우치는밤에 ISTJ      ISTJ  이런 유형의 비슷한 질문이 있기는 했지만 대부분 ISTJ 남자와 잘맞을 거 같은 여...
0       ISFP 용가리      ISFP  학교 말듣 숙제로 백상예술대상을 조사해 가야 하는데 어떻게 해야 할지 잘 모르겠어요...

[600 rows x 3 columns]